In [2]:
import os
import gc
from tqdm import tqdm
import pandas as pd
import geopandas as gpd
import numpy as np
from shapely.geometry import LineString
import matplotlib.pyplot as plt

In [2]:
def get_ookla_nuts_level(nuts, read_root, folder, file, eu_range):
    # read ookla data, reproject and calculate the area of each tile
    print(read_root + r'/' + folder + r'/' + file)
    ookla_global = gpd.read_file(read_root + r'/' + folder + r'/' + file)
    ookla_global.to_crs('EPSG:3035', inplace = True)
    ookla_global['Shape_Area'] = ookla_global.area    
    
    # extract ookla polygon to centroids
    ookla_global.geometry = ookla_global['geometry'].centroid

    # musk the centroids by NUTS boundary
    ookla = gpd.clip(ookla_global, eu_range)
    del ookla_global
    gc.collect()

    # calculate the average download and upload data of all ookla points that fall within certain NUTS region
    speed_dict = {}
    unit = 'kbps'
    freq = 'quarter'
    for nuts_id in tqdm(nuts['NUTS_ID']):
        area = nuts[nuts['NUTS_ID']==nuts_id]
        ookla_within = gpd.sjoin(ookla, area, how='inner')
        if len(ookla_within)<1:
            avg_d_kpbs = 'NA'
            avg_u_kbps = 'NA'
        else:
            ookla_within['area*d'] = ookla_within['avg_d_kbps']*ookla_within['Shape_Area']
            ookla_within['area*u'] = ookla_within['avg_u_kbps']*ookla_within['Shape_Area']
            avg_d_kpbs = ookla_within['area*d'].sum()/ookla_within['Shape_Area'].sum()
            avg_u_kbps = ookla_within['area*u'].sum()/ookla_within['Shape_Area'].sum()
        speed_dict[nuts_id] = [quarter, network_type, unit, freq, avg_d_kpbs, avg_u_kbps, year]

    # delete ookla and release the RAM
    del ookla
    gc.collect()
    
    return speed_dict    

In [13]:
if __name__ == "__main__":
    eu_range = gpd.read_file('/data/xiang/1-Data/NUTS/eu.shp')
    nuts_folder = '/data/xiang/1-Data/NUTS/nuts version'
    for nuts_file in os.listdir(nuts_folder):
        if nuts_file.endswith('.shp'):
            print(nuts_file)
            nuts = gpd.read_file(nuts_folder + r'/' + nuts_file)        
            read_root = '/data/xiang/1-Data/Ookla'
            save_folder = '/data/xiang/3-case studies/0-ookla data/separate quarters_NUTS' + nuts_file.split('_')[-2]
            for folder in tqdm(os.listdir(read_root)): 
                if folder+'.csv' in os.listdir(save_folder):
                    continue
                else:
                    for file in os.listdir(read_root + '//' + folder):
                        if file.endswith('.shp'):
                            # get the input variable from file paths
                            year = folder.split('-')[0]
                            quarter = int(folder.split('-')[1])//3+1
                            network_type = folder.split('_')[-2]
            
                            #  concatenante df from different quarters and years into one
                            speed_dict = get_ookla_nuts_level(nuts, read_root, folder, file, eu_range)
                            speed_df = pd.DataFrame(speed_dict).T
                            speed_df.reset_index(inplace=True)
                            speed_df.columns = ['geo', 'quarter', 'network_type', 'unit', 'freq', 'download', 'upload', 'obsTime']
            
                            # reshape the df and save it
                            reshap_df = pd.melt(speed_df, id_vars=['geo', 'quarter', 'unit', 'freq', 'obsTime','network_type'], value_vars = ['download', 'upload'], var_name = 'direction', value_name = 'obsValue')
                            reshap_df.to_csv('/data/xiang/3-case studies/0-ookla data/separate quarters_NUTS' + nuts_file.split('_')[-2] + r'/' + folder + '.csv')

    for nuts_file in os.listdir(nuts_folder):
        # concatenate all csv of separate quarters into a full csv and export it
        quarter_path = '/data/xiang/3-case studies/0-ookla data/separate quarters_NUTS' + nuts_file.split('_')[-2]
        df_concat = None
        for quarter_file in os.listdir(quarter_path):
            if quarter_file.endswith('.csv'):
                df_temp = pd.read_csv(quarter_path + r'/' + quarter_file, index_col=0)
                df_concat = df_temp if df_concat is None else pd.concat([df_concat, df_temp])
                
        df_concat.to_csv('/data/xiang/3-case studies/0-ookla data/ookla_nuts' + nuts_file.split('_')[-2] + '.csv', na_rep='NA')    

NUTS_RG_01M_2010_3035.shp


100%|████████████████████████████████████████| 42/42 [00:00<00:00, 27383.92it/s]


NUTS_RG_01M_2006_3035.shp


100%|████████████████████████████████████████| 42/42 [00:00<00:00, 35042.92it/s]


NUTS_RG_01M_2013_3035.shp


...


 95%|██████████████████████████████████▎ | 40/42 [22:52:53<1:09:57, 2098.93s/it]

/data/xiang/1-Data/Ookla/2020-01-01_performance_mobile_tiles/gps_mobile_tiles.shp



 98%|█████████████████████████████████████ | 41/42 [23:16:30<31:34, 1894.16s/it]

/data/xiang/1-Data/Ookla/2022-01-01_performance_mobile_tiles/gps_mobile_tiles.shp



100%|██████████████████████████████████████| 42/42 [23:39:04<00:00, 2027.26s/it]
